# Update exposure data with user-input data

This notebook demonstrates how to update the exposure data in an existing Delft-FIAT model with user-input data. Examples will be shown about how to update the ground floor height and the max potential damages (this will be added later!).

## **Step 0**: Import required packages
First we need to import the necessary python packages.

In [25]:
from hydromt_fiat.fiat import FiatModel
from hydromt.log import setuplog
from pathlib import Path
import shutil
import geopandas as gpd
from hydromt.gis_utils import utm_crs

## **Step 1**: Configure
The first step is to set up the configuration needed to initialize the FIAT model. Begin by specifying where the model that should be updated is saved, locating the required data catalog, and setting up the logger.

In [2]:
model_folder = Path().absolute() / "data" / "update_ground_floor_height" / "fiat_model"
data_catalog = Path().absolute() / "data" / "hydromt_fiat_catalog_USA.yml"
logger = setuplog("hydromt_fiat", log_level=10)

2023-10-18 13:36:08,112 - hydromt_fiat - log - INFO - HydroMT version: 0.8.0


## **Step 2**: Initialize and read existing model
In this step we initialize HydroMT-FIAT in read-mode (`mode="r"`) with the `model_folder`, `data_catalog`, and `logger` that we defined above. We also read in the existing dummy model.

In [3]:
fm = FiatModel(root=model_folder, mode="r", data_libs=[data_catalog], logger=logger)
fm.read()

2023-10-18 13:36:08,144 - hydromt_fiat - data_catalog - INFO - Parsing data catalog from c:\Repositories\hydromt_fiat\examples\data\hydromt_fiat_catalog_USA.yml
2023-10-18 13:36:08,148 - hydromt_fiat - log - DEBUG - Appending log messages to file c:\Repositories\hydromt_fiat\examples\data\update_ground_floor_height\fiat_model\hydromt.log.
2023-10-18 13:36:08,148 - hydromt_fiat - model_api - INFO - Initializing fiat model from hydromt_fiat (v0.2.1.dev0).
2023-10-18 13:36:08,149 - hydromt_fiat - fiat - INFO - Reading model data from c:\Repositories\hydromt_fiat\examples\data\update_ground_floor_height\fiat_model
2023-10-18 13:36:08,150 - hydromt_fiat - model_api - DEBUG - User defined config read from c:\Repositories\hydromt_fiat\examples\data\update_ground_floor_height\fiat_model\settings.toml
2023-10-18 13:36:08,150 - hydromt_fiat - fiat - INFO - Reading model table files.
2023-10-18 13:36:08,151 - hydromt_fiat - fiat - DEBUG - Reading vulnerability table c:\Repositories\hydromt_fiat\e

## **Step 3**: Update the Ground Floor Height of the exposure data
Next, we will update the Ground Floor Height of some of the exposure assets in our model. We have created some ficticious data that represents elevation certificates. We will first inspect the current exposure data and ground floor heights and the "elevation certificate" data.

As can be seen below, apparently the ground floor height of all assets is set to 1 (foot).

In [5]:
original_exposure = fm.exposure.get_full_gdf(fm.exposure.exposure_db)
original_exposure["Ground Floor Height"].unique()

array([1], dtype=int64)

Now we will load the "elevation certificate" data and visualize it together with the exposure assets below on the map.

In [42]:
elevation_certificates_path = (
    Path().absolute()
    / "data"
    / "update_ground_floor_height"
    / "fake_elevation_certificates.gpkg"
)
elevation_certificates = gpd.read_file(elevation_certificates_path)

# Plot the exposure and elevation certificates data
m = elevation_certificates.explore(column="FFE", cmap="Reds", style_kwds={"radius": 5})
m = original_exposure.explore(m=m, column="Ground Floor Height", cmap="Reds")
m

We will use a maximum distance of 10 meter to join the elevation certificate data to their nearest building. The attribute in the elevation certificate data that we need to use is `FFE`, which stands for First Floor Elevation and is often used in the US to indicate the Ground Floor Height with.

In [20]:
attribute = "FFE"
method = "nearest"
max_dist = 50

fm.exposure.setup_ground_floor_height(
    ground_floor_height=elevation_certificates_path,
    attr_name=attribute,
    method=method,
    max_dist=max_dist,
)

2023-10-18 13:51:17,288 - hydromt_fiat - data_catalog - INFO - DataCatalog: Getting fake_elevation_certificates GeoDataFrame vector data from c:\Repositories\hydromt_fiat\examples\data\update_ground_floor_height\fake_elevation_certificates.gpkg
2023-10-18 13:51:17,293 - hydromt_fiat - geodataframe - INFO - GeoDataFrame: Read vector data.


## **Step 4**: Check the resulting exposure data
As you can see below, the ground floor height of the exposure assets also contains other values.

In [24]:
updated_exposure = fm.exposure.get_full_gdf(fm.exposure.exposure_db)
updated_exposure["Ground Floor Height"].unique()

array([ 1,  2, 11, 20, 10, 12], dtype=int64)

We will make a buffer of 10 meter around the 

In [39]:
# Check if the Ground Floor Heigh attribute is set correctly
nearest_utm = utm_crs(elevation_certificates.total_bounds)
elevation_certificates_projected = elevation_certificates.to_crs(nearest_utm)
elevation_certificates_projected.geometry = (
    elevation_certificates_projected.geometry.buffer(max_dist)
)

# Plot the exposure and elevation certificates data
m = elevation_certificates_projected.explore(column="FFE", cmap="Reds")
m = updated_exposure.explore(m=m, column="Ground Floor Height", cmap="Reds")
m

## **Step 5**: Save the updated FIAT model
Set the folder where you want to save the model to and write it to that folder.

In [43]:
save_folder = (
    Path().absolute() / "data" / "update_ground_floor_height" / "updated_fiat_model"
)

# Remove the new root folder if it already exists
if save_folder.exists():
    shutil.rmtree(save_folder)

# Set the new root and write the model
fm.set_root(save_folder)
fm.write()

2023-10-18 15:53:42,160 - hydromt_fiat - log - DEBUG - Writing log messages to new file c:\Repositories\hydromt_fiat\examples\data\update_ground_floor_height\updated_fiat_model\hydromt.log.
2023-10-18 15:53:42,161 - hydromt_fiat - fiat - INFO - Updating all data objects...
2023-10-18 15:53:42,162 - hydromt_fiat - model_api - WARNING - Replacing geom: building_points
2023-10-18 15:53:42,163 - hydromt_fiat - fiat - INFO - Writing model data to c:\Repositories\hydromt_fiat\examples\data\update_ground_floor_height\updated_fiat_model
2023-10-18 15:53:42,163 - hydromt_fiat - model_api - INFO - Writing model config to c:\Repositories\hydromt_fiat\examples\data\update_ground_floor_height\updated_fiat_model\settings.toml
2023-10-18 15:53:42,165 - hydromt_fiat - model_api - DEBUG - Writing file exposure/building_points.gpkg
2023-10-18 15:53:42,256 - hydromt_fiat - fiat - INFO - Writing model vulnerability_curves table file to vulnerability/vulnerability_curves.csv.
2023-10-18 15:53:42,260 - hydr